In [60]:
import requests
from requests_file import FileAdapter

project_name = "k9mail"

s = requests.Session()
s.mount('file://', FileAdapter())

# Make a GET request to fetch the JSON data
response = s.get("file:///D:/Research/javapers/sample_output/k9mail.json")

# Convert the response to JSON format
data = response.json()

data

{'elements': {'nodes': [{'data': {'id': 'com.fsck.k9.activity.compose.RecipientLoader.PROJECTION_CRYPTO_ADDRESSES',
     'properties': {'sourceText': 'private static final java.lang.String[] PROJECTION_CRYPTO_ADDRESSES = new java.lang.String[]{ "address", "uid_address" };',
      'visibility': 'private',
      'simpleName': 'PROJECTION_CRYPTO_ADDRESSES',
      'kind': 'field',
      'metaSrc': 'source code'},
     'labels': ['Variable']}},
   {'data': {'id': 'com.fsck.k9.activity.ActivityListener.pendingCommandsProcessing(com.fsck.k9.Account).account',
     'properties': {'simpleName': 'account',
      'kind': 'parameter',
      'metaSrc': 'source code'},
     'labels': ['Variable']}},
   {'data': {'id': 'com.fsck.k9.provider.DecryptedFileProvider.getUriForProvidedFile(android.content.Context,java.io.File,java.lang.String,java.lang.String).file',
     'properties': {'simpleName': 'file',
      'kind': 'parameter',
      'metaSrc': 'source code'},
     'labels': ['Variable']}},
   {'dat

In [2]:
def transform_graph(graph):
	nodes = { node['data']['id']: node['data'] for node in graph['elements']['nodes'] }
	edges = {}
	for edge in graph['elements']['edges']:
		if 'label' in edge['data']:
			label = edge['data']['label']
		else:
			label = ','.join(edge['data']['labels'])
			edge['data']['label'] = label
		
		if label not in edges:
			edges[label] = []
		edges[label].append(edge['data'])
	return (nodes, edges)
	

In [4]:
nodes, edges = transform_graph(data)

list(nodes.keys()), list(edges.keys())

(['com.fsck.k9.activity.compose.RecipientLoader.PROJECTION_CRYPTO_ADDRESSES',
  'com.fsck.k9.activity.ActivityListener.pendingCommandsProcessing(com.fsck.k9.Account).account',
  'com.fsck.k9.provider.DecryptedFileProvider.getUriForProvidedFile(android.content.Context,java.io.File,java.lang.String,java.lang.String).file',
  'com.fsck.k9.view.ToolableViewAnimator.com.fsck.k9.view.ToolableViewAnimator(android.content.Context,android.util.AttributeSet,int).context',
  'com.fsck.k9.activity.Accounts$ImportSelectionDialog.show(com.fsck.k9.activity.Accounts).activity',
  'com.fsck.k9.view.CryptoModeSelector$CryptoModeSelectorState.SIGN_ONLY',
  'com.fsck.k9.activity.MessageInfoHolder.compareDate',
  'com.fsck.k9.Account.setDraftsFolderName(java.lang.String).name',
  'com.fsck.k9.fragment.MessageListFragmentComparators$DateComparator.com.fsck.k9.fragment.MessageListFragmentComparators$DateComparator()',
  'com.fsck.k9.message.AutocryptStatusInteractor$RecipientAutocryptStatusType.canEncrypt',


In [24]:
def invert(edgeList):
    prefix = "inv_"
    return [{**edge,
            'source': edge['target'],
            'target': edge['source'],
            'label': prefix + edge.get('label', 'edge'),
        } for edge in edgeList]

# invert(edges['contains'])

In [25]:
def compose(l1, l2, newlabel=None):
    mapping = {
        edge['source']: {
            'target': edge['target'], 
            'label': edge.get('label','edge1'), 
            'weight': edge.get('properties', {}).get('weight', 1)
        } for edge in l2 }
    
    result = {}
    for edge in l1:
        s1 = edge['source']
        t1 = edge['target']
        label = edge.get('label', 'edge2')
        properties = edge.get('properties', {})
        mappingEntry = mapping.get(t1)

        if mappingEntry:
            newWeight = mappingEntry['weight'] * properties.get('weight', 1)
            key = (s1, mappingEntry['target'])
            if key not in result:
                result[key] = {
                    'source': s1,
                    'target': mappingEntry['target'],
                    'label': newlabel or label + "-" + mappingEntry['label'],
                    'properties': {'weight': newWeight},
                }
            else:
                result[key]['properties']['weight'] += newWeight
    return list(result.values())


contains = [
    {"source": "class A", "target": "method x"},
    {"source": "class A", "target": "method x2"},
    {"source": "class B", "target": "method y"}
]

invokes = [
    {"source": "method x", "target": "method y"},
    {"source": "method x2", "target": "method y"}
]

inverted_contains = invert(contains)

calls = compose(compose(contains, invokes), inverted_contains)

calls


[{'source': 'class A',
  'target': 'class B',
  'label': 'edge2-edge1-inv_edge',
  'properties': {'weight': 2}}]

In [33]:
def get_all_labels(objects):
    labels = set()
    for obj in objects.values():
        if 'labels' in obj and isinstance(obj['labels'], list):
            labels.update(obj['labels'])
    return labels

get_all_labels(nodes)

{'Constructor',
 'Container',
 'Operation',
 'Primitive',
 'Script',
 'Structure',
 'Variable'}

In [27]:
def get_edge_node_labels(edge, nodes):
    src_labels = nodes.get(edge['source'], {}).get('labels', [])
    tgt_labels = nodes.get(edge['target'], {}).get('labels', [])

    return [(src_label, tgt_label) for src_label in src_labels for tgt_label in tgt_labels]

get_edge_node_labels(edges['invokes'][0], nodes)

[('Operation', 'Operation')]

In [28]:
def get_source_and_target_labels(edge_list, nodes):
    edge_node_labels = {label for edge in edge_list for label in get_edge_node_labels(edge, nodes)}

    return edge_node_labels

get_source_and_target_labels(edges['invokes'], nodes)

{('Constructor', 'Constructor'),
 ('Constructor', 'Operation'),
 ('Operation', 'Constructor'),
 ('Operation', 'Operation')}

In [29]:
def get_ontology(edges, nodes):
    return {label: get_source_and_target_labels(edge, nodes) for label, edge in edges.items()}

get_ontology(edges, nodes)

{'type': {('Variable', 'Primitive'), ('Variable', 'Structure')},
 'invokes': {('Constructor', 'Constructor'),
  ('Constructor', 'Operation'),
  ('Operation', 'Constructor'),
  ('Operation', 'Operation')},
 'hasParameter': {('Constructor', 'Variable'), ('Operation', 'Variable')},
 'hasScript': {('Structure', 'Constructor'),
  ('Structure', 'Operation'),
  ('Structure', 'Script')},
 'returnType': {('Constructor', 'Structure'),
  ('Operation', 'Primitive'),
  ('Operation', 'Structure')},
 'hasVariable': {('Structure', 'Variable')},
 'contains': {('Container', 'Container'),
  ('Container', 'Structure'),
  ('Structure', 'Structure')},
 'instantiates': {('Constructor', 'Structure'),
  ('Operation', 'Structure'),
  ('Script', 'Structure')},
 'specializes': {('Structure', 'Structure')}}

In [37]:
def lift(rel1, rel2, newlabel=None):
    return compose(compose(rel1, rel2), invert(rel1), newlabel)

lift(contains, invokes)

[{'source': 'class A',
  'target': 'class B',
  'label': 'edge2-edge1-inv_edge',
  'properties': {'weight': 2}}]

In [31]:
get_all_labels(nodes)

{'Constructor',
 'Container',
 'Operation',
 'Primitive',
 'Script',
 'Structure',
 'Variable'}

In [34]:
get_source_and_target_labels(edges['invokes'], nodes)

{('Constructor', 'Constructor'),
 ('Constructor', 'Operation'),
 ('Operation', 'Constructor'),
 ('Operation', 'Operation')}

In [35]:
get_ontology(edges,nodes)

{'type': {('Variable', 'Primitive'), ('Variable', 'Structure')},
 'invokes': {('Constructor', 'Constructor'),
  ('Constructor', 'Operation'),
  ('Operation', 'Constructor'),
  ('Operation', 'Operation')},
 'hasParameter': {('Constructor', 'Variable'), ('Operation', 'Variable')},
 'hasScript': {('Structure', 'Constructor'),
  ('Structure', 'Operation'),
  ('Structure', 'Script')},
 'returnType': {('Constructor', 'Structure'),
  ('Operation', 'Primitive'),
  ('Operation', 'Structure')},
 'hasVariable': {('Structure', 'Variable')},
 'contains': {('Container', 'Container'),
  ('Container', 'Structure'),
  ('Structure', 'Structure')},
 'instantiates': {('Constructor', 'Structure'),
  ('Operation', 'Structure'),
  ('Script', 'Structure')},
 'specializes': {('Structure', 'Structure')}}

In [38]:
calls = lift(edges['hasScript'], edges['invokes'], 'calls')
calls

[{'source': 'com.fsck.k9.activity.compose.MessageActions',
  'target': 'com.fsck.k9.activity.compose.MessageActions',
  'label': 'calls',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.ui.crypto.MessageCryptoHelper',
  'target': 'com.fsck.k9.mailstore.MessageHelper',
  'label': 'calls',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.message.SimpleMessageBuilder',
  'target': 'com.fsck.k9.message.MessageBuilder',
  'label': 'calls',
  'properties': {'weight': 2}},
 {'source': 'com.fsck.k9.service.BootReceiver',
  'target': 'com.fsck.k9.service.CoreReceiver',
  'label': 'calls',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.activity.setup.AuthTypeHolder',
  'target': 'com.fsck.k9.activity.setup.AuthTypeHolder',
  'label': 'calls',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.K9',
  'target': 'com.fsck.k9.Account$SortType',
  'label': 'calls',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.ui.messageview.MessageTopView',
  'target': 'co

In [39]:
constructs = compose(edges['hasScript'], edges['instantiates'], 'constructs')
constructs

[{'source': 'com.fsck.k9.fragment.MessageListFragment',
  'target': 'com.fsck.k9.activity.MessageReference',
  'label': 'constructs',
  'properties': {'weight': 4}},
 {'source': 'com.fsck.k9.ui.crypto.MessageCryptoHelper',
  'target': 'com.fsck.k9.ui.crypto.MessageCryptoHelper$CryptoPart',
  'label': 'constructs',
  'properties': {'weight': 4}},
 {'source': 'com.fsck.k9.activity.FolderList$FolderListAdapter',
  'target': 'com.fsck.k9.activity.FolderList$FolderViewHolder',
  'label': 'constructs',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.helper.RetainFragment',
  'target': 'com.fsck.k9.helper.RetainFragment',
  'label': 'constructs',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.remotecontrol.K9RemoteControl',
  'target': 'com.fsck.k9.remotecontrol.AccountReceiver',
  'label': 'constructs',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.helper.K9AlarmManager',
  'target': 'com.fsck.k9.power.DozeChecker',
  'label': 'constructs',
  'properties': {'wei

In [41]:
holds = compose(edges['hasVariable'], edges['type'], "holds")
holds

[{'source': 'com.fsck.k9.widget.list.MessageListRemoteViewFactory$MailItem',
  'target': 'java.lang.String',
  'label': 'holds',
  'properties': {'weight': 3}},
 {'source': 'com.fsck.k9.activity.MessageList',
  'target': 'com.fsck.k9.mailstore.StorageManager$StorageListener',
  'label': 'holds',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.ui.crypto.MessageCryptoHelper$State',
  'target': 'com.fsck.k9.ui.crypto.MessageCryptoHelper$State',
  'label': 'holds',
  'properties': {'weight': 5}},
 {'source': 'com.fsck.k9.activity.compose.AttachmentPresenter',
  'target': 'com.fsck.k9.activity.compose.AttachmentPresenter$AttachmentsChangedListener',
  'label': 'holds',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.fragment.MessageListFragment',
  'target': 'com.fsck.k9.Preferences',
  'label': 'holds',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.ui.messageview.MessageTopView',
  'target': 'int',
  'label': 'holds',
  'properties': {'weight': 3}},
 {'source':

In [42]:
accepts = compose(edges['hasScript'], compose(edges['hasParameter'], edges['type']), "accepts")
accepts

[{'source': 'com.fsck.k9.fragment.MessageListFragment',
  'target': 'int',
  'label': 'accepts',
  'properties': {'weight': 19}},
 {'source': 'com.fsck.k9.activity.compose.MessageActions',
  'target': 'boolean',
  'label': 'accepts',
  'properties': {'weight': 2}},
 {'source': 'com.fsck.k9.K9',
  'target': 'com.fsck.k9.Account$SortType',
  'label': 'accepts',
  'properties': {'weight': 3}},
 {'source': 'com.fsck.k9.ui.messageview.MessageTopView',
  'target': 'com.fsck.k9.mailstore.MessageViewInfo',
  'label': 'accepts',
  'properties': {'weight': 6}},
 {'source': 'com.fsck.k9.controller.MessagingController',
  'target': 'com.fsck.k9.mailstore.LocalFolder',
  'label': 'accepts',
  'properties': {'weight': 7}},
 {'source': 'com.fsck.k9.controller.MessagingController',
  'target': 'com.fsck.k9.controller.MessagingListener',
  'label': 'accepts',
  'properties': {'weight': 17}},
 {'source': 'com.fsck.k9.activity.FolderList$FolderListAdapter',
  'target': 'int',
  'label': 'accepts',
  'pro

In [43]:
returns = compose(edges['hasScript'], edges['returnType'], "returns")
returns

[{'source': 'com.fsck.k9.fragment.MessageListFragment',
  'target': 'com.fsck.k9.activity.MessageReference',
  'label': 'returns',
  'properties': {'weight': 3}},
 {'source': 'com.fsck.k9.service.BootReceiver',
  'target': 'com.fsck.k9.service.BootReceiver',
  'label': 'returns',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.activity.setup.AuthTypeHolder',
  'target': 'java.lang.String',
  'label': 'returns',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.K9',
  'target': 'boolean',
  'label': 'returns',
  'properties': {'weight': 47}},
 {'source': 'com.fsck.k9.Account',
  'target': 'int',
  'label': 'returns',
  'properties': {'weight': 14}},
 {'source': 'com.fsck.k9.activity.setup.AuthTypeAdapter',
  'target': 'int',
  'label': 'returns',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.helper.MergeCursorWithUniqueId',
  'target': 'long',
  'label': 'returns',
  'properties': {'weight': 2}},
 {'source': 'com.fsck.k9.service.CoreService',
  'target': 'int'

## Fix for nested classes

To make our life easier, let's change an edge label: "contains" is now only for packages to other packages or classes, while classes to classes is changed into "nests".

In [44]:
nested_classes_set = set(
    edge['target'] for edge in edges['contains']
    if 'Structure' in nodes.get(edge['source'], {}).get('labels', []))
nested_classes_set

{'com.fsck.k9.Account$DeletePolicy',
 'com.fsck.k9.Account$Expunge',
 'com.fsck.k9.Account$FolderMode',
 'com.fsck.k9.Account$MessageFormat',
 'com.fsck.k9.Account$QuoteStyle',
 'com.fsck.k9.Account$Searchable',
 'com.fsck.k9.Account$ShowPictures',
 'com.fsck.k9.Account$SortType',
 'com.fsck.k9.K9$ApplicationAware',
 'com.fsck.k9.K9$BACKGROUND_OPS',
 'com.fsck.k9.K9$Intents',
 'com.fsck.k9.K9$Intents$EmailReceived',
 'com.fsck.k9.K9$Intents$Share',
 'com.fsck.k9.K9$LockScreenNotificationVisibility',
 'com.fsck.k9.K9$NotificationHideSubject',
 'com.fsck.k9.K9$NotificationQuickDelete',
 'com.fsck.k9.K9$SplitViewMode',
 'com.fsck.k9.K9$Theme',
 'com.fsck.k9.PRNGFixes$LinuxPRNGSecureRandom',
 'com.fsck.k9.PRNGFixes$LinuxPRNGSecureRandomProvider',
 'com.fsck.k9.Throttle$MyTimerTask',
 'com.fsck.k9.Throttle$MyTimerTask$HandlerRunnable',
 'com.fsck.k9.activity.AccountList$AccountsAdapter',
 'com.fsck.k9.activity.AccountList$AccountsAdapter$AccountViewHolder',
 'com.fsck.k9.activity.AccountLis

In [45]:
top_level_classes = [
    node_id for node_id, node in nodes.items()
    if 'Structure' in node.get('labels', []) and node_id not in nested_classes_set
]

top_level_classes_set = set(top_level_classes)

top_level_classes_set

{'com.fsck.k9.Account',
 'com.fsck.k9.AccountStats',
 'com.fsck.k9.BaseAccount',
 'com.fsck.k9.Clock',
 'com.fsck.k9.EmailAddressValidator',
 'com.fsck.k9.FontSizes',
 'com.fsck.k9.Globals',
 'com.fsck.k9.Identity',
 'com.fsck.k9.K9',
 'com.fsck.k9.NotificationSetting',
 'com.fsck.k9.PRNGFixes',
 'com.fsck.k9.Preferences',
 'com.fsck.k9.Throttle',
 'com.fsck.k9.account.AccountCreator',
 'com.fsck.k9.activity.AccountList',
 'com.fsck.k9.activity.Accounts',
 'com.fsck.k9.activity.ActivityListener',
 'com.fsck.k9.activity.AlternateRecipientAdapter',
 'com.fsck.k9.activity.ChooseAccount',
 'com.fsck.k9.activity.ChooseFolder',
 'com.fsck.k9.activity.ChooseIdentity',
 'com.fsck.k9.activity.ColorPickerDialog',
 'com.fsck.k9.activity.ConfirmationDialog',
 'com.fsck.k9.activity.EditIdentity',
 'com.fsck.k9.activity.EmailAddressList',
 'com.fsck.k9.activity.FolderInfoHolder',
 'com.fsck.k9.activity.FolderList',
 'com.fsck.k9.activity.FolderListFilter',
 'com.fsck.k9.activity.K9Activity',
 'com.f

In [47]:
new_contains = [edge for edge in edges['contains'] if edge['source'] not in top_level_classes_set]
new_contains

[{'id': '205549359078d0bdd1b8c38ad76aa98d',
  'source': 'com.fsck.k9',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 'source code'},
  'target': 'com.fsck.k9.message'},
 {'id': 'd3c405e6527dfaa75148a4b5c936dc5b',
  'source': 'com.fsck.k9.helper',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 'source code'},
  'target': 'com.fsck.k9.helper.jsoup'},
 {'id': 'fa0327f2187fb8fc7e5b5b3095b13d76',
  'source': 'com.fsck.k9.provider',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 'source code'},
  'target': 'com.fsck.k9.provider.UnreadWidgetProvider'},
 {'id': '226e1a2a371736b4d61e023529354022',
  'source': 'com.fsck.k9.fragment',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 'source code'},
  'target': 'com.fsck.k9.fragment.MessageListFragmentComparators$AttachmentComparator'},
 {'id': '25565d064f1bcffa78a247bf4ca1cd07',
  'source': 'com.fsck.k9.ui.crypto',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 's

In [49]:
nests = edges['nests'] \
		if 'nests' in edges \
		else [dict(edge, label="nests") 
				for edge in edges['contains'] 
				if edge['source'] in top_level_classes_set]
nests

[{'id': 'b1c5870260ff02de2f00cbf20c499f42',
  'source': 'com.fsck.k9.preferences.AccountSettings',
  'label': 'nests',
  'properties': {'containmentType': 'nested class',
   'weight': 1,
   'metaSrc': 'source code'},
  'target': 'com.fsck.k9.preferences.AccountSettings$StorageProviderSetting'},
 {'id': '15a67e4043ff2970803bd342dd8e8586',
  'source': 'com.fsck.k9.provider.MessageProvider',
  'label': 'nests',
  'properties': {'containmentType': 'nested class',
   'weight': 1,
   'metaSrc': 'source code'},
  'target': 'com.fsck.k9.provider.MessageProvider$AccountNumberExtractor'},
 {'id': '30c2a10219b9e23887ab5b9807155924',
  'source': 'com.fsck.k9.K9',
  'label': 'nests',
  'properties': {'containmentType': 'nested class',
   'weight': 1,
   'metaSrc': 'source code'},
  'target': 'com.fsck.k9.K9$ApplicationAware'},
 {'id': 'a7796bc25b89a412c166709684dbf91e',
  'source': 'com.fsck.k9.fragment.ConfirmationDialogFragment',
  'label': 'nests',
  'properties': {'containmentType': 'nested cla

In [51]:
depends_calls = [edge for edge in lift(new_contains, calls, "depends_calls") if edge['source'] != edge['target']]
depends_holds = [edge for edge in lift(new_contains, holds, "depends_holds") if edge['source'] != edge['target']]
depends_constructs = [edge for edge in lift(new_contains, constructs, "depends_constructs") if edge['source'] != edge['target']]
depends_accepts = [edge for edge in lift(new_contains, accepts, "depends_accepts") if edge['source'] != edge['target']]

depends = depends_calls + depends_holds + depends_constructs + depends_accepts
depends

[{'source': 'com.fsck.k9.provider',
  'target': 'com.fsck.k9.helper',
  'label': 'depends_calls',
  'properties': {'weight': 2}},
 {'source': 'com.fsck.k9.ui.crypto',
  'target': 'com.fsck.k9.mailstore',
  'label': 'depends_calls',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.crypto',
  'target': 'com.fsck.k9.ui.crypto',
  'label': 'depends_calls',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.fragment',
  'target': 'com.fsck.k9.search',
  'label': 'depends_calls',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.helper',
  'target': 'com.fsck.k9',
  'label': 'depends_calls',
  'properties': {'weight': 7}},
 {'source': 'com.fsck.k9.activity',
  'target': 'com.fsck.k9.controller',
  'label': 'depends_calls',
  'properties': {'weight': 2}},
 {'source': 'com.fsck.k9.activity.setup',
  'target': 'com.fsck.k9.helper',
  'label': 'depends_calls',
  'properties': {'weight': 1}},
 {'source': 'com.fsck.k9.provider',
  'target': 'com.fsck.k9.mailstore',
  'label': 

In [52]:
def filter_objects_by_labels(data, labels):
    filtered_data = {}
    for key, object in data.items():
        if any(label in labels for label in object['labels']):
            filtered_data[key] = object
    return filtered_data


In [53]:
abstract_nodes = filter_objects_by_labels(nodes, ["Container", "Structure", "Primitive", "Problem"])
abstract_edges = {
    'contains': new_contains,
    'specializes': edges['specializes'],
    'nests': nests,
    'calls': calls,
    'constructs': constructs,
    'holds': holds,
    'accepts': accepts,
    'returns': returns,
}

abstract_nodes, abstract_edges

({'com.fsck.k9.mailstore.migrations.MigrationTo31': {'id': 'com.fsck.k9.mailstore.migrations.MigrationTo31',
   'properties': {'docComment': '',
    'simpleName': 'MigrationTo31',
    'kind': 'class',
    'metaSrc': 'source code'},
   'labels': ['Structure']},
  'long': {'id': 'long',
   'properties': {'simpleName': 'long', 'metaSrc': 'source code'},
   'labels': ['Primitive']},
  'com.fsck.k9.activity.setup.AccountSettings': {'id': 'com.fsck.k9.activity.setup.AccountSettings',
   'properties': {'docComment': '',
    'simpleName': 'AccountSettings',
    'kind': 'class',
    'metaSrc': 'source code'},
   'labels': ['Structure']},
  'com.fsck.k9.fragment.MessageListFragment$FolderOperation': {'id': 'com.fsck.k9.fragment.MessageListFragment$FolderOperation',
   'properties': {'docComment': '',
    'simpleName': 'FolderOperation',
    'kind': 'enum',
    'metaSrc': 'source code'},
   'labels': ['Structure']},
  'com.fsck.k9.provider.AttachmentTempFileProvider$AttachmentTempFileProviderClea

In [54]:
abstract_graph = {
    'elements': {
        'nodes': [{'data':node} for node in abstract_nodes.values()],
        'edges': [{'data':edge} for edge_list in abstract_edges.values() for edge in edge_list],
    },
}

abstract_graph['elements']


{'nodes': [{'data': {'id': 'com.fsck.k9.mailstore.migrations.MigrationTo31',
    'properties': {'docComment': '',
     'simpleName': 'MigrationTo31',
     'kind': 'class',
     'metaSrc': 'source code'},
    'labels': ['Structure']}},
  {'data': {'id': 'long',
    'properties': {'simpleName': 'long', 'metaSrc': 'source code'},
    'labels': ['Primitive']}},
  {'data': {'id': 'com.fsck.k9.activity.setup.AccountSettings',
    'properties': {'docComment': '',
     'simpleName': 'AccountSettings',
     'kind': 'class',
     'metaSrc': 'source code'},
    'labels': ['Structure']}},
  {'data': {'id': 'com.fsck.k9.fragment.MessageListFragment$FolderOperation',
    'properties': {'docComment': '',
     'simpleName': 'FolderOperation',
     'kind': 'enum',
     'metaSrc': 'source code'},
    'labels': ['Structure']}},
  {'data': {'id': 'com.fsck.k9.provider.AttachmentTempFileProvider$AttachmentTempFileProviderCleanupReceiver',
    'properties': {'docComment': '',
     'simpleName': 'AttachmentT

In [55]:
def get_edges_with_labels(nodes, edge_list, label):
    # Filter edge_list to include only edges where both source and target nodes have label "Container"
    filtered_edges = [edge for edge in edge_list if label in nodes[edge['source']].get('labels', []) and label in nodes[edge['target']].get('labels', [])]
    return filtered_edges


In [56]:
get_edges_with_labels(nodes, edges['contains'], 'Container')

[{'id': '205549359078d0bdd1b8c38ad76aa98d',
  'source': 'com.fsck.k9',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 'source code'},
  'target': 'com.fsck.k9.message'},
 {'id': 'd3c405e6527dfaa75148a4b5c936dc5b',
  'source': 'com.fsck.k9.helper',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 'source code'},
  'target': 'com.fsck.k9.helper.jsoup'},
 {'id': '6c6b12a50ada3c230e425ddc5685ce27',
  'source': 'com.fsck.k9',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 'source code'},
  'target': 'com.fsck.k9.power'},
 {'id': 'f28e711956eb7c3b04b300ef5c294a48',
  'source': 'com.fsck.k9.message',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 'source code'},
  'target': 'com.fsck.k9.message.extractors'},
 {'id': 'c83a25607e7ffa307d7200c8c946c2a5',
  'source': 'com.fsck.k9',
  'label': 'contains',
  'properties': {'weight': 1, 'metaSrc': 'source code'},
  'target': 'com.fsck.k9.provider'},
 {'id': '13465b03eb3e67e90b739eaeb0

In [57]:
pkg_nodes = filter_objects_by_labels(nodes, ["Container", "Problem"])
pkg_edges = {
    'contains': get_edges_with_labels(nodes, edges['contains'], "Container"),
    'depends': depends
}

pkg_edges


{'contains': [{'id': '205549359078d0bdd1b8c38ad76aa98d',
   'source': 'com.fsck.k9',
   'label': 'contains',
   'properties': {'weight': 1, 'metaSrc': 'source code'},
   'target': 'com.fsck.k9.message'},
  {'id': 'd3c405e6527dfaa75148a4b5c936dc5b',
   'source': 'com.fsck.k9.helper',
   'label': 'contains',
   'properties': {'weight': 1, 'metaSrc': 'source code'},
   'target': 'com.fsck.k9.helper.jsoup'},
  {'id': '6c6b12a50ada3c230e425ddc5685ce27',
   'source': 'com.fsck.k9',
   'label': 'contains',
   'properties': {'weight': 1, 'metaSrc': 'source code'},
   'target': 'com.fsck.k9.power'},
  {'id': 'f28e711956eb7c3b04b300ef5c294a48',
   'source': 'com.fsck.k9.message',
   'label': 'contains',
   'properties': {'weight': 1, 'metaSrc': 'source code'},
   'target': 'com.fsck.k9.message.extractors'},
  {'id': 'c83a25607e7ffa307d7200c8c946c2a5',
   'source': 'com.fsck.k9',
   'label': 'contains',
   'properties': {'weight': 1, 'metaSrc': 'source code'},
   'target': 'com.fsck.k9.provider'}

In [58]:
pkg_graph = {
    "elements": {
        "nodes": [ {"data": node} for node in list(pkg_nodes.values()) ],
        "edges": [ {"data": edge} for edge in sum(list(pkg_edges.values()), []) ]
    }
}

pkg_graph["elements"]

{'nodes': [{'data': {'id': 'com.fsck.k9.ui.compose',
    'properties': {'simpleName': 'compose',
     'kind': 'package',
     'metaSrc': 'source code'},
    'labels': ['Container']}},
  {'data': {'id': 'com.fsck.k9',
    'properties': {'simpleName': 'k9',
     'kind': 'package',
     'metaSrc': 'source code'},
    'labels': ['Container']}},
  {'data': {'id': 'com.fsck.k9.mailstore.util',
    'properties': {'simpleName': 'util',
     'kind': 'package',
     'metaSrc': 'source code'},
    'labels': ['Container']}},
  {'data': {'id': 'com.fsck.k9.controller',
    'properties': {'simpleName': 'controller',
     'kind': 'package',
     'metaSrc': 'source code'},
    'labels': ['Container']}},
  {'data': {'id': 'com.fsck.k9.activity.compose',
    'properties': {'simpleName': 'compose',
     'kind': 'package',
     'metaSrc': 'source code'},
    'labels': ['Container']}},
  {'data': {'id': 'com.fsck.k9.message.html',
    'properties': {'simpleName': 'html',
     'kind': 'package',
     'metaS

In [59]:
import json

def write_json(dictionary, file_path):
  with open(file_path, 'w') as json_file:
    json.dump(dictionary, json_file, indent=2)

In [ ]:
write_json(project_name+"-cls-output.json",abstract_graph)

In [ ]:
write_json(project_name+"-pkg-output.json",pkg_graph)